In [43]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.layouts import gridplot
from bokeh.models import Span
from scipy.interpolate import PchipInterpolator
from scipy.optimize import minimize, curve_fit
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
import warnings
warnings.filterwarnings('ignore')
output_notebook()

def plot_format(plot, xlabel, ylabel, location, size, titlesize, labelsize):
    # x axis format
    plot.xaxis.axis_label = xlabel
    plot.xaxis.axis_label_text_font_size = size
    plot.xaxis.axis_line_color = '#282B30'
    plot.xaxis.major_tick_line_color = '#DAE3F3'
    plot.xaxis.minor_tick_line_color = '#DAE3F3'
    plot.xaxis.major_label_text_font_size = size
    
    # y axis format
    plot.yaxis.axis_label = ylabel
    plot.yaxis.axis_label_text_font_size = size
    plot.yaxis.major_label_text_font_size = size
    plot.yaxis.axis_line_color = '#282B30'
    
    # Legend format
    plot.legend.location = location
    plot.legend.click_policy = "hide"
    plot.legend.label_text_font_size = labelsize
    plot.legend.border_line_width = 3
    plot.legend.border_line_color = "navy"
    plot.legend.border_line_alpha = 0.0
    plot.legend.background_fill_alpha = 0.0
    plot.legend.label_text_color = "#E3F4FF"

    # Title format
    plot.title.text_font_size = titlesize
    plot.title.text_font_style = "bold"
    plot.outline_line_color = '#282B30'

    # Dark theme
    plot.background_fill_color = "#282B30"
    plot.border_fill_color = "#282B30"
    plot.xgrid.grid_line_color = '#606773'
    # plot.xgrid.minor_grid_line_color = '#606773' 
    # plot.xgrid.minor_grid_line_alpha = 0.4
    # plot.xgrid.minor_grid_line_dash = [2, 2] 
    plot.xaxis.minor_tick_line_color = '#606773'
    plot.yaxis.minor_tick_line_color = '#606773'
    plot.ygrid.grid_line_color = '#606773'
    plot.yaxis.major_label_text_color = "#E3F4FF"
    plot.xaxis.major_label_text_color = "#E3F4FF"
    plot.yaxis.axis_label_text_color = "#E3F4FF"
    plot.xaxis.axis_label_text_color = "#E3F4FF"
    plot.title.text_color = "#A6DDFF"
    return plot

new_colors = []
for i in range(42):
        new_colors.append('#9D6C97')
        new_colors.append('#9DC3E6')
        new_colors.append('#9DD9C5')
        new_colors.append('#F2DDA4')
        new_colors.append('#C4A287')


Loading BokehJS ...

## 3D plot

The goal of this project is to measure wafer roughness using scattered light. So far, this has been done by measuring the roughness from a very smooth surface and using this data as a reference base function. Then, this base function is combined with a background/roughness function in order to reconstruct the experimental data. The reconstruction is based on minimization methods with the purpose of finding the best fit parameters. The method has worked well, however there is still an error in the data reconstruction. In order to solve this, a new data set has been acquired by rotating the wafer along the vertical axis of rotation using a computer controlled rotation stepper motor as shown in Fig. @fig-10 .



::: {#fig-10}

![](images/f/Fig_10.png)

Optosurf data acquisition
:::

By rotating the wafer along the vertical axis of rotation the peak of the roughness function is translated along the degrees axis of the optosurf as a function of the mechanical angle of rotation. Hence, we can relate the this angle with the angle shift in the optosurf degrees angle. The obtained dataset was acquired with a rotation angle of 10 degrees and 1024 steps. Due to the double angle of reflection, the acquired data set is now shown in a 20 deg range:

In [44]:
offaxis = np.arange(-512, 512, 1)*20/1024 + 1.82
onaxis=np.arange(-15.5,16.5,1)

# 1. Generate 3d plots
def subplot3d(files, df_slice, slices, offaxis, onaxis):
    """
    Generates a 3D plot of the data

    Parameters
    ----------
    files (list): List of files to plot
    df_slice (dataframe): Dataframe with the slices to plot
    
    Returns
    -------
    subplot (plotly.graph_objects.Figure): Plotly figure with the 3D plot
    spots (dict): Dictionary with the data of the files
    """
    # a. Define on and off axis as well as subplots
    subplot = make_subplots(rows=1, cols=2, subplot_titles=(file1, file1), 
                    specs=[[{'type': 'surface'}, {'type': 'scatter'}]])
    x = np.linspace(0, 10, 100)
    z = np.linspace(0, 10, 100)
    y = np.linspace(-15.5, 15.5, 100)
    X, Z = np.meshgrid(x, z)
    Y, Z2 = np.meshgrid(y, z)
    count = 0
    spots = {}
    col = 1

    # b. Read file and create matrix
    for file in files:
        # c. Read the .csv file
        vals = np.genfromtxt(file, delimiter=',')
        
        # d. Normalize values
        normalized_vals = vals[:, 1:] 
        normalized_vals = 10 * vals[:, 1:] / np.max(np.max(vals[:, 1:]))
        
        # e. 3D surface plot
        surface = go.Surface(x=offaxis, y=onaxis, z=normalized_vals, colorscale='jet', 
                   showscale=True)

        # f. Add slice to subplot
        for i, row in df_slice.iterrows():
            slice_off_ind = int(row.slice)
            slice_on = go.Surface(x=offaxis[slice_off_ind]*np.ones_like(Y), y=Y, z=Z2, opacity=0.3, showscale=False, colorscale='Greys')
            subplot.add_trace(slice_on, row=1, col=col)
            subplot.add_trace(go.Scatter(x=onaxis, y=vals[:,slice_off_ind], mode="lines", name=f'On-axis {col}'), row=1, col=2)

        for slice in slices:
            slice_off_ind = slice
            slice_on = go.Surface(x=offaxis[slice]*np.ones_like(Y), y=Y, z=Z2, opacity=0.6, showscale=False, colorscale='Viridis')
            subplot.add_trace(slice_on, row=1, col=col)
        subplot.add_trace(surface, row=1, col=col)
        col += 1    

        # g. Create dictionary
        spots[file] = vals
    return subplot, spots

file1 = "data/f/" + 'Rotate_Ann7_onaxis_10degscan.csv'
edited_df = pd.DataFrame({"slice": [50, 250, 500, 750, 1000]})
edited_df["degree"] = offaxis[edited_df["slice"].astype(int)]
slice_1 = 100
slice_2 = 900
subplot, spots = subplot3d([file1], edited_df, [slice_1, slice_2], offaxis, onaxis)
subplot.update_scenes(camera_eye=dict(x=-0.75, y=-2.25, z=1.25))
subplot.update_layout(width=1200, height=600)
subplot


The acquired dataset opens new analysis posibilities. The x axis represents the mechanical rotation axis (20 degrees), while the y axis is the optosurf degrees axis (32 acquisition points). The z axis represent the signal intensity. The advantage of this scanning method is that now there are 1024 traces that can be obtained from cross-section planes, additionaly, the mechanical rotation angle is known, hence the shift along the optosurf axis can be calculated more accurately.

## Minimization/cost function
Once the dataset has been acquired, the [minimization method](d_minimization_strategies.ipynb) previously defined can be applied in order to estimate the x0 displacement. In this case, the effect of the background function is ignored. In the 3D dataset several grayscale planes have been drawn, this planes represent the cross-sections with 32 sampling points coming from the optosurf linear array. Applying the miminization method yields:

In [45]:
# 5. Define cost function
def cost_function(params, y):
    """
    Generates a 3D plot of the data

    Parameters
    ----------
    params (list): List of parameters to fit
    y (array): Array with the data to fit
    
    Returns
    -------
    rmse (float): Root mean square error of the fit0.

    """
    if background_bool == True:
        x0, A0, sigma, A1, n, displacement = params
        x_new = onaxis + x0
        # interpolate base function with respect to x_new (32 points)
        y_base_modified = A0*pchip(x_new) 
        # y_base_modified = A0*pchip(onaxis) 
        # calculate background on original axis and with x0
        y_background = supergaussian(x_new, x0+displacement, sigma, A1, n)
        # y_background = supergaussian(onaxis, x0, sigma, A1, n)
        # calculate modi    fied function
        y_modified = y_base_modified + y_background

    else:
        x0, A0 = params
        x_new = onaxis + x0
        y_modified = A0*pchip(x_new) 

    if weight_bool:
       mse = np.mean(np.abs(onaxis)*((y - y_modified) ** 2))
       rmse = np.sqrt(mse)  
    else:
        mse = np.mean((y - y_modified) ** 2)
        rmse = np.sqrt(mse)
    # convergence.append(rmse)
    return rmse

# Get reference base function and define pchip
smooth_df = pd.read_csv("data/f/smooth_df.csv")
x_base = smooth_df['xaxis']
y_base = smooth_df['yaxis']
pchip = PchipInterpolator(x_base, y_base)


# 7. Define super-gaussian function
supergaussian = lambda x, x0, sigma, A1, n: A1 * np.exp(-abs(((x-x0)/sigma))**n)

# 8. Define optimization parameters
# methods = ['Powell', 'CG', 'L-BFGS-B', 'SLSQP', 'trust-constr']
method = 'Powell'

# 9. Get matrix 32*1024
vals = spots['data/f/Rotate_Ann7_onaxis_10degscan.csv']
optimized_plot = figure(title = 'Optimized plot', width = 700, height = 450, tooltips = [("index", "$index"),("(x,y)", "($x, $y)")])
count = 0 
background_bool = False
weight_bool = False

# edited_df = edited_df.reset_index()
index = ['angle', 'x0', 'Abase', 'sigma', 'Agaussian', 'n', 'displacement', 'error']
columns = ["s_" + str(int(x)) for x in list(edited_df['slice'])]
optimized_df = pd.DataFrame(columns=columns, index=index)

# bounds = ((-15, 15), (-0.5, 1.2), (1, 4), (-1000, None), (1, 4), (-3, 3))

# # 10. Loop through the selected slices
for i, row in edited_df.iterrows():
        # 11. Define initial guess
        slice_off_ind = int(row.slice)
        x0 = offaxis[slice_off_ind]
        Abase = 1.0
        sigma = 1.0
        Agaussian = 1000.0
        n = 1
        displacement = 0.5
        guess = [x0, Abase, sigma, Agaussian, n, displacement]
        guess_no_back = [x0, Abase]
        
        # 12. Call minimize function
        y = vals[:,slice_off_ind]
        cost_fn = lambda p:cost_function(p, y)
        if background_bool:
            # Minimize
            result = minimize(cost_fn, guess, method=method, bounds=bounds)
            optimized_parameters = list(result.x)
            x0_opt, A0_opt, sigma_opt, A1_opt, n_opt, displacement = optimized_parameters

            # Calculate optimized function
            x_new_opt = onaxis + x0_opt
            y_base_opt = A0_opt*pchip(x_new_opt) 
            y_background_opt = supergaussian(x_new_opt, x0_opt, sigma_opt, A1_opt, n_opt)
            y_optimized = y_base_opt + y_background_opt

            # Calculate error
            mse = np.mean((y - y_optimized) ** 2)
            rmse = np.sqrt(mse)
            optimized_parameters.append(rmse)

            # Create optmized parameters table
            column = "s_" + str(int(row.slice))
            optimized_parameters.insert(0, row.degree)
            optimized_df[column] = optimized_parameters

        else:
            # Minimize
            result = minimize(cost_fn, guess_no_back, method=method,)
            optimized_parameters = list(result.x)
            x0_opt, A0_opt, = optimized_parameters

            # Calculate optimized function
            optimized_parameters.insert(0, row.degree)
            x_new_opt = onaxis + (x0_opt)
            y_optimized = A0_opt*pchip(x_new_opt) 

            # Calculate error
            mse = np.mean((y - y_optimized) ** 2)
            rmse = np.sqrt(mse)

            # Create optmized parameters table
            column = "s_" + str(int(row.slice))
            optimized_parameters.extend([0, 0, 0, 0, rmse])
            optimized_df[column] = optimized_parameters

        # 14. Plot experimental data
        optimized_plot.line(x=onaxis, y=vals[:,slice_off_ind], line_width=4.5, 
                            legend_label=f'{offaxis[slice_off_ind]:.4f} ({slice_off_ind})', color=new_colors[i])
        optimized_plot.circle(x=onaxis, y=vals[:,slice_off_ind], size = 8,
                              legend_label=f'{offaxis[slice_off_ind]:.4f} ({slice_off_ind})', color = '#65757B')

        # 15. Plot optimized data
        optimized_plot.line(onaxis, y_optimized, line_width = 5, color=new_colors[i+1], 
                            legend_label=f'{slice_off_ind} optimized', dash='dashed')
        optimized_plot.triangle(onaxis, y_optimized, size = 8,
                            legend_label=f'{slice_off_ind} optimized')
        vline = Span(location=0.0, dimension = 'height', line_color='#508AA8', line_width=1)
        optimized_plot.add_layout(vline)

optimized_plot = plot_format(optimized_plot, "Degrees", "Intensity", "top_right", "10pt", "11pt", "8pt")
show(optimized_plot)

In [46]:
display(optimized_df)

s_50      s_250      s_500       s_750      s_1000
angle          -7.203437  -3.297187   1.585625    6.468438   11.351250
x0             -6.884040  -3.168367   1.508667    6.175089   10.621863
Abase           0.987824   0.988666   0.987914    0.984152    0.921566
sigma           0.000000   0.000000   0.000000    0.000000    0.000000
Agaussian       0.000000   0.000000   0.000000    0.000000    0.000000
n               0.000000   0.000000   0.000000    0.000000    0.000000
displacement    0.000000   0.000000   0.000000    0.000000    0.000000
error         163.536177  26.649583  44.802124  192.763391  912.815973

## Slice section minimization

It is now proposed to apply the minimization method to the 3D dataset. In order to do so, the previously calculated [base function](c_experimental_data.ipynb) is used as a starting point. The parameters to be optimimized are the x0 displacement and the amplitude of the base function. The obtained results are shown in the following figure:

In [47]:
# 5. Define cost function
def cost_function(params, y):
    """
    Generates a 3D plot of the data

    Parameters
    ----------
    params (list): List of parameters to fit
    y (array): Array with the data to fit
    
    Returns
    -------
    rmse (float): Root mean square error of the fit0.
    """
    x0, A0 = params
    x_new = onaxis + x0
    y_modified = A0*pchip(x_new) 

    if weight_bool:
       mse = np.mean(np.abs(onaxis)*((y - y_modified) ** 2))
       rmse = np.sqrt(mse)  
    else:
        mse = np.mean((y - y_modified) ** 2)
        rmse = np.sqrt(mse)
    # convergence.append(rmse)
    return rmse

slices = np.arange(20, 1000, step=1)
minimized_df = pd.DataFrame(columns=["angle", "x0", "difference", "slice", "amplitude", "rmse"])
# methods = ['Powell', 'CG', 'L-BFGS-B', 'SLSQP', 'trust-constr']
method = 'Powell'

for j, slice in enumerate(slices):
    x0 = offaxis[slice]
    Abase = 1.0
    sigma = 1.0
    Agaussian = 1000.0
    n = 1
    displacement = 0.5
    guess = [x0, Abase, sigma, Agaussian, n, displacement]
    guess_no_back = [x0, Abase]

    # Call minimization function
    y = vals[:,slice]
    cost_fn = lambda p:cost_function(p, y)

    result = minimize(cost_fn, guess_no_back, method=method,)
    optimized_parameters = list(result.x)
    x0_opt, A0_opt, = optimized_parameters

    # Calculate optimized function
    x_new_opt = onaxis + (x0_opt)
    y_optimized = A0_opt*pchip(x_new_opt) 

    # Calculate error
    mse = np.mean((y - y_optimized) ** 2)
    rmse = np.sqrt(mse)
    row = [offaxis[slice], x0_opt, offaxis[slice] - x0_opt, slice, A0_opt, rmse]
    minimized_df.loc[j] = row

def linear_function(x, m , b):
    return m*x + b

angle = minimized_df['angle']
x0 = minimized_df['x0']
difference = minimized_df['difference']

# rotation angle vs. x0 linear fit
coef, covariance = curve_fit(linear_function, angle, x0)   
slope = coef[0]
intercept = coef[1]
angle = np.arctan(slope)
angle_degrees = np.degrees(angle)

# x0 vs difference fit
poly = PolynomialFeatures(degree=3)
x0 = minimized_df['x0'].values
x0_poly = poly.fit_transform(x0.reshape(-1,1))
model = LinearRegression().fit(X=x0_poly, y=difference)
xaxis = np.arange(-15.5, 15.5, 0.1)
xaxis_poly = poly.transform(xaxis.reshape(-1,1))
ypredictions = model.predict(xaxis_poly)

# Estimate angle differences
onaxis_poly = poly.transform(onaxis.reshape(-1,1))
y_shifted = model.predict(onaxis_poly)
shifted_axis = onaxis + y_shifted

p1 = figure(title=f'a. Rotation angle vs. x0 (x0 = {slope:.2f}*Rotation angle {intercept:.2f})')
p1.line(x=minimized_df['x0'], y=minimized_df['angle'], line_width=2, color = new_colors[0])
p1.xaxis.ticker.desired_num_ticks = 10
p1 = plot_format(p1, "Rotation angle", "x0", "top_right", "10pt", "8pt", "8pt")\

p2 = figure(title='c. Rotation angle vs. RMSE')
p2.line(x=minimized_df['angle'], y=minimized_df['rmse'], line_width=2, color = new_colors[1])
p2.xaxis.ticker.desired_num_ticks = 10
p2 = plot_format(p2, "Rotation angle", "RMSE", "top_right", "10pt", "11pt", "8pt")

p3 = figure(title='b. x0 vs. difference (x0-angle)')
p3.line(x=minimized_df['x0'], y=minimized_df['difference'], line_width=2, color = new_colors[2])
p3.line(x=xaxis, y=ypredictions, line_width=2, color = new_colors[4], dash='dashed')
p3.xaxis.ticker.desired_num_ticks = 10
p3 = plot_format(p3, "x0", "difference", "top_right", "10pt", "11pt", "8pt")

p4 = figure(title='d. Rotation angle vs. amplitude')
p4.line(x=minimized_df['angle'], y=minimized_df['amplitude'], line_width=2, color = new_colors[4])
p4.xaxis.ticker.desired_num_ticks = 10
p4 = plot_format(p4, "Rotation angle", "amplitude", "top_right", "10pt", "11pt", "8pt")

grid = gridplot(children=[p1, p2, p3, p4], ncols=2, merge_tools=False, width = 350, height = 340)
show(grid)


The minimimization method was applied across the rotation axis by obtaining cross-section datasets, each with 32 sampling points. The minimization method estimated two parameters: x0 and the amplitude of the base function. 

* Plot a shows x0 as a function of the rotation angle, notice this have a linear relationship. 
* Plot b shows the difference as a function of x0, where difference is defined as rotation angle - x0, this no longer has a linear relationship but instead a 3rd order polynomial was fit. 
* Plot c shows the RMSE as a function a rotation angle, notice it increases for angles beyond 6 degrees.
* Plot d shows the optimized amplitute as a function of rotation angle, notice there is a sudden decrease in amplitute beyond 10 degrees.

In [48]:
from IPython.core.display import HTML
minimized_html = minimized_df.to_html(max_rows=10)
display(HTML(minimized_html))

## Shifted axis

The relevant plot to relate the rotation angle with the x0 displacement is plot b. From this plot, we can relate the x0 displacement with a well know rotation angle, hence we can estimate the difference or error in the optosurf degrees axis. The estimated shifted axis is now shown: 

In [49]:
p5 = figure(title='Shifted optosurf axis', width=1000, height=350, y_range=(-0.2, 0.9))
p5.circle(x=shifted_axis, y=np.zeros(len(onaxis))+0.5, line_width=2, color = new_colors[6], size = 7, legend_label="Shifted axis")
p5.circle(x=onaxis, y=np.zeros(len(onaxis)), line_width=2, color = new_colors[5], size = 7, legend_label="Original axis")
p5.xaxis.ticker.desired_num_ticks = 40
p5 = plot_format(p5, "Angle", "angle", "top_right", "10pt", "11pt", "8pt")

show(p5)

The shifted axis shows that there is a spread in the optosurf axis. With the new shifted axis it is possible to replot the optosurf32 sampling points with the correct angle axis, e.g. (solid lines are the date with the shifted axis):

In [50]:
shifted_plot = figure(title = 'Shifted plot', width = 1000, height = 450, tooltips = [("index", "$index"),("(x,y)", "($x, $y)")])
for i, row in edited_df.iterrows():
    slice_off_ind = int(row.slice)
    y = vals[:,slice_off_ind]
    shifted_plot.line(x=onaxis, y=y, line_width=4.5, 
                            legend_label=f'Original: {offaxis[slice_off_ind]:.4f} ({slice_off_ind})', color=new_colors[i], dash='dashed', alpha = 0.5)
    shifted_plot.circle(x=onaxis, y=y, size = 8,
                            legend_label=f'Original: {offaxis[slice_off_ind]:.4f} ({slice_off_ind})', color = '#65757B')
    shifted_plot.line(x=shifted_axis, y=y, line_width=4.5, 
                            legend_label=f'Shifted: {offaxis[slice_off_ind]:.4f} ({slice_off_ind})', color=new_colors[i],)
    shifted_plot.triangle(x=shifted_axis, y=y, size = 8,
                            legend_label=f'Shifted: {offaxis[slice_off_ind]:.4f} ({slice_off_ind})', color = '#65757B')
shifted_plot = plot_format(shifted_plot, "Angle", "Amplitude", "top_right", "10pt", "11pt", "8pt")     
show(shifted_plot)

## Base function

In [51]:
base_1 = 20
base_2 = 900
base_step = 1
slices_base = np.arange(base_1, base_2+1, step=base_step)
minimized_df_2 = minimized_df.set_index(minimized_df['slice'])

# Recenter experimental data with respect to new shifted axis and rotation angle
x_base = []
y_base = []
slice_array = []
for k, slice in enumerate(slices_base):
    y = vals[:,slice]
    x0 = minimized_df_2.loc[slice, 'x0']
    angle = minimized_df_2.loc[slice, 'angle']
    amp = minimized_df_2.loc[slice, 'amplitude']
    y = y/amp
    shifted_axis_2 = shifted_axis + angle
    # shifted_axis_2 = onaxis + difference
    # shifted_axis_2 = shifted_axis + x0 + difference
    x_base.extend(list(shifted_axis_2))
    y_base.extend(list(y))
    slice_array.extend(np.ones(len(shifted_axis_2))*slice)

# 'Raw' base function
base_function_df = pd.DataFrame({'xaxis': x_base, 'yaxis': y_base, 'slice': slice_array})
base_function_df = base_function_df.sort_values(by='xaxis')


# Average points calculation
x_filtered = base_function_df['xaxis'].values
y_filtered = base_function_df['yaxis'].values
window_size = 0.06
x_averaged = []
y_averaged = []
left = -5
right = 5
base_plot_2 = figure(title = 'Base function clusters', x_range = (left, right), width = 1300, height = 500, tooltips = [("index", "$index"),("(x,y)", "($x, $y)")])
# loop through x_filtered with a window size 
for i in np.arange(np.min(x_filtered), np.max(x_filtered), window_size):
    # get the indices of the points within the current window
    indices = np.where((x_filtered >= i) & (x_filtered < i + window_size))[0]
    if len(indices) == 0:
        continue
    # calculate the average x and y values for the points in the current window
    x_avg = np.mean(x_filtered[indices])
    y_avg = np.mean(y_filtered[indices])
    # append the averaged x and y values to the lists
    x_averaged.append(x_avg)
    y_averaged.append(y_avg)
x_averaged = np.array(x_averaged)
y_averaged = np.array(y_averaged)

# Average points interpolation
f = PchipInterpolator(x_averaged, y_averaged)
x_interp = np.linspace(x_averaged[0], x_averaged[-1], num=5000)
y_interp = f(x_interp)

# Plot points, average and interpolation
base_plot_2.circle(x=x_filtered, y=y_filtered, size=5.5, color = new_colors[1], legend_label='Original')
base_plot_2.line(x=x_interp, y=y_interp, line_width=5.5,  
                 color = new_colors[5], legend_label='Interpolation')
base_plot_2.circle(x=x_averaged, y=y_averaged, size=5.5, color = '#EC5766', legend_label='Averaged')

base_plot_2 = plot_format(base_plot_2, "Angle", "Amplitude", "top_right", "10pt", "11pt", "8pt")
base_plot_2.xaxis.ticker.desired_num_ticks = 20

# Plot by sections
new_colors = []
for i in range(42):
        new_colors.append('#ffadad')
        new_colors.append('#ffd6a5')
        new_colors.append('#caffbf')
        new_colors.append('#9bf6ff')
        new_colors.append('#bdb2ff')
        new_colors.append('#ffc6ff')

def sections_plot(plot, df):
    for z, row in df.iterrows():
        slices = np.arange(int(row['start']), int(row['end']+1), step=1)
        amplitudes = minimized_df.loc[slices]['amplitude']
        # st.write(amplitudes)
        mask = base_function_df['slice'].isin(slices)
        sliced_df = base_function_df.loc[mask]
        sliced_df.sort_values(by=['slice', 'xaxis'], inplace=True)
        # st.write(sliced_df)
        for k, amp in amplitudes.iteritems():
            internal_slice = int(k)
            sliced_df_2 = sliced_df[sliced_df['slice'] == internal_slice]
            sliced_df_2['yaxis'] = sliced_df_2['yaxis'] / amp
            plot.circle(x=sliced_df_2['xaxis'], y=sliced_df_2['yaxis'], size=6, 
                                   color = new_colors[z], legend_label=f'{int(row.start)} to {int(row.end)} amp')
    plot.circle(x=x_averaged, y=y_averaged, size=5.5, color = '#EC5766', legend_label='Averaged')
    plot = plot_format(plot, "Angle", "Amplitude", "top_right", "10pt", "11pt", "8pt")
    return plot

# base_sections.xaxis.ticker.desired_num_ticks = 20

sections_df = pd.DataFrame({'start': [300, 326, 351, 376, 401, 426], 
                            'end':   [325, 350, 375, 400, 425, 450]})
base_sections = figure(title = 'Base function sections', x_range = (left, right),
                        width = 1300, height = 800, tooltips = [("index", "$index"),("(x,y)", "($x, $y)")])

base_sections = sections_plot(base_sections, sections_df)

sections_df_b = pd.DataFrame({'start': [20, 51, 101, 151, 201, 251], 
                            'end':   [50, 100, 150, 200, 250, 300]})
base_sections_b = figure(title = 'Base function sections', x_range = (left, right),
                        width = 1300, height = 800, tooltips = [("index", "$index"),("(x,y)", "($x, $y)")])

base_sections_b  = sections_plot(base_sections_b, sections_df_b)


grid_base = gridplot(children=[base_sections, base_sections_b, base_plot_2], ncols = 1, merge_tools=False, width=850, height=450)
show(grid_base)